# The Calliope model and backend objects

In this tutorial, we use the urban scale example model to go into a bit more detail on the public and non-public properties of the `calliope.Model` and `calliope.Model.backend` objects.

In [ ]:
from pathlib import Path

import calliope

calliope.set_log_verbosity("INFO", include_solver_output=False)

# Model input

In [ ]:
# Initialise the model with the Urban Scale example model
m = calliope.examples.urban_scale()

In [ ]:
# Get information on the model
print(m.info())

## Model definition dictionary

`m._model_def_dict` is a python dictionary that holds all the data from the model definition YAML files, restructured into one dictionary.

The underscore before the method indicates that it defaults to being hidden (i.e. you wouldn't see it by trying a tab auto-complete and it isn't documented)

In [ ]:
m._model_def_dict.keys()

`techs` hold only the information about a technology that is specific to that node

In [ ]:
m._model_def_dict["techs"]["pv"]

`nodes` hold only the information about a technology that is specific to that node

In [ ]:
m._model_def_dict["nodes"]["X2"]["techs"]["pv"]

## Model data

`m._model_data` is an xarray Dataset.
Like `_model_def_dict` it is a hidden prperty of the Model as you are expected to access the data via the public property `inputs`

In [ ]:
m.inputs

Until we solve the model, `inputs` is the same as `_model_data`

In [ ]:
m._model_data

We can find the same PV `flow_cap_max` data as seen in `m._model_run`

In [ ]:
m._model_data.flow_cap_max.sel(techs="pv").to_series().dropna()

# Building and checking the optimisation problem

Calling `m.build` allows us to build the optimisation problem, which creates arrays of Python objects from the YAML math formulation.

In [ ]:
m.build()

As with the calliope `Model`, the backend has its own dataset containing all the arrays of backend objects

In [ ]:
m.backend._dataset

There is then a public API to access filtered views on this dataset, e.g. input parameters...

In [ ]:
m.backend.parameters

... or constraints

In [ ]:
m.backend.constraints

You can also access backend arrays in text format, to debug the problem:

In [ ]:
m.backend.get_constraint(
    "area_use_capacity_per_loc", as_backend_objs=False
).to_pandas().dropna(how="all", axis=0)

We can increase the verbosity of the constraint/global expression "body" by calling the backend method `verbose_strings`.
We do not do this automatically as it entails a memory/time overhead on building the model and is only necessary for debugging your optimisation problem.

In [ ]:
m.backend.verbose_strings()
m.backend.get_constraint(
    "area_use_capacity_per_loc", as_backend_objs=False
).to_pandas().dropna(how="all", axis=0)

## Updating the optimisation problem in-place

If we want to update a parameter value or fix a decision variable, we can do so now that we have built the optimisation problem

In [ ]:
m.backend.update_parameter("flow_cap_max", m.inputs.flow_cap_max * 2)
m.backend.get_parameter("flow_cap_max", as_backend_objs=False).sel(
    techs="pv"
).to_series().dropna()

## Solve the optimisation problem

Once we have all of our optimisation problem components set up as we desire, we can solve the problem.

In [ ]:
m.solve()

The results are stored in `m._model_data` and can be accessed by the public property `m.results`

In [ ]:
m.results

We can also view the data within the backend directly

In [ ]:
m.backend.get_variable("flow_cap", as_backend_objs=False).to_series().dropna()

# Save

In [ ]:
# We can save at any point, which will dump the entire m._model_data to file.
# NetCDF is recommended, as it retains most of the data and can be reloaded into a Calliope model at a later date.


output_path = Path(".") / "outputs" / "4_calliope_model_object"
output_path.mkdir(parents=True, exist_ok=True)

m.to_netcdf(output_path / "example.nc")  # Saves a single file
m.to_csv(
    output_path / "csv_files", allow_overwrite=True
)  # Saves a file for each xarray DataArray